# Tipos de Dados, Marcas Gráficas e Canais de Codificação Visual (José)

A visualização representa a informação usando uma coleção de _marcas gráficas_ (barras, linhas, pontos, etc.). Os atributos de uma marca - como sua posição, formato, tamanho, ou cor - servem como _canais_ através dos quais podemos codificar valores de dados subjacentes.

Com uma estrutura de tipos de dados, marcas e canais de codificação, podemos criar de forma concisa uma grande variedade de visualizações. Nesse notebook, exploramos cada um desses elementos e mostramos como usá-los para criar gráficos estatísticos customizados.

_Esse notebook é parte do [currículo de visualização de dados](https://github.com/uwdata/visualization-curriculum)._


In [1]:
import pandas as pd
import altair as alt

##  Dados de Desenvolvimento Global (José)
Vamos visualizar dados de saúde global e população para vários países, no período de 1955 à 2005. Os dados foram coletados pela [Fundação Gapminder](https://www.gapminder.org/) e compartilhados na [famosa palestra TED de Hans Rosling](https://www.youtube.com/watch?v=hVimVzgtD6w). Se você ainda não a assistiu, recomendamos que o faça primeiro!

Primeiro, vamos carregar o conjunto de dados da coleção [vega-datasets](https://github.com/vega/vega-datasets) em um _data frame_ do Pandas.

In [3]:
from vega_datasets import data as vega_data
data = vega_data.gapminder()

Quão grande são os dados?

In [4]:
data.shape

(693, 6)

693 linhas e 6 colunas. Vamos dar uma olhada no conteúdo:

In [5]:
data.head(5)

year      country  cluster       pop  life_expect  fertility
0  1955  Afghanistan        0   8891209       30.332        7.7
1  1960  Afghanistan        0   9829450       31.997        7.7
2  1965  Afghanistan        0  10997885       34.020        7.7
3  1970  Afghanistan        0  12430623       36.088        7.7
4  1975  Afghanistan        0  14132019       38.438        7.7


Para cada país (<span style="color:deeppink">country</span>) e ano (<span style="color:deeppink">year</span>) (em intervalos de 5 anos), temos medidas de números de crianças por mulher (<span style="color:deeppink">fertility</span>), espectativa de vida (<span style="color:deeppink">life_expect</span>) e total de população (<span style="color:deeppink">pop</span>).

Há também uma coluna chamada grupo (<span style="color:deeppink">cluster</span>) com códigos inteiros. Vamos descobrir o que isso representa ao longo da visualização!

Também vamos criar um _data frame_ de dados menor, filtrando somente os valores do anos 2000:

In [6]:
data2000 = data.loc[data['year'] == 2000]

In [7]:
data2000.head(5)

year      country  cluster       pop  life_expect  fertility
9   2000  Afghanistan        0  23898198       42.129     7.4792
20  2000    Argentina        3  37497728       74.340     2.3500
31  2000        Aruba        3     69539       73.451     2.1240
42  2000    Australia        4  19164620       80.370     1.7560
53  2000      Austria        1   8113413       78.980     1.3820

## Tipos de dados (José)

O primeiro ingrediente para uma visualização eficaz são os dados de entrada. Os valores de dados podem representar diferentes formas de medição.
Que tipos de comparações essas medições suportam? E que tipos de codificações visuais apoiam essas comparações?

Começaremos analisando os tipos básicos de dados que o Altair usa para informar as escolhas de codificação visual. Esses tipos de dados determinam os tipos de comparações que podemos fazer e, assim, orientam nossas decisões no design de visualizações.



### Nominal (N) (Arthur Zanetti)

Dados _nominais_ (também chamados de dados _categóricos_) consistem em nomes de categorias.

Com dados nominais, podemos comparar a igualdade dos valores: _o valor A é igual ou diferente do valor B? (A = B)_, permitindo afirmações como “A é igual a B” ou “A não é igual a B”. No conjunto de dados acima, o campo país (<span style="color:deeppink">country</span>) é nominal.

Ao visualizar dados nominais, devemos ser capazes de identificar facilmente se os valores são iguais ou diferentes: posição, matiz de cor (azul, vermelho, verde, etc.) e forma podem ajudar. No entanto, usar o canal de tamanho para codificar dados nominais pode nos enganar, sugerindo diferenças de ordem ou magnitude entre valores que não existem!

### Ordinal (O) (Arthur Zanetti)

Dados _ordinais_ consistem em valores que possuem uma ordenação específica.

Com dados ordinais, podemos comparar a ordenação dos valores: _o valor A vem antes ou depois do valor B? (A < B)_, permitindo afirmações como “A é menor que B” ou “A é maior que B”. No conjunto de dados acima, podemos tratar o campo ano (<span style="color:deeppink">year</span>) como ordinal.

Ao visualizar dados ordinais, devemos perceber um senso de ordenação. Posição, tamanho ou valor da cor (brilho) podem ser apropriados, enquanto matiz de cor (que não é perceptualmente ordenada) seria menos adequado.


### Quantitativo (Q) (Arthur Zanetti)

Com dados *quantitativos*, podemos medir diferenças numéricas entre valores. Existem vários subtipos de dados quantitativos:

Para dados *intervalares*, podemos medir a distância (intervalo) entre pontos: *qual é a distância do valor A ao valor B? (A - B)*, permitindo afirmações como “A está 12 unidades distante de B”.

Para dados *proporcionais*, o ponto zero é significativo, e assim podemos medir proporções ou fatores escalares:*o valor A corresponde a qual proporção do valor B? (A / B)*, permitindo afirmações como “A é 10% de B” ou “B é 7 vezes maior que A”.

No conjunto de dados acima, ano (<span style="color:deeppink">year</span>) é um campo quantitativo intervalar (o valor de “zero” no ano é subjetivo), enquanto fecundidade (<span style="color:deeppink">fertility</span>) e expectativa de vida (<span style="color:deeppink">life_expect</span>) são campos quantitativos proporcionais (zero é significativo para o cálculo de proporções). O Vega-Lite representa dados quantitativos, mas não faz distinção entre os tipos intervalares e proporcionais.

Valores quantitativos podem ser visualizados usando posição, tamanho ou valor da cor, entre outros canais. Um eixo com uma linha de base em zero é essencial para comparações proporcionais de valores proporcionais, mas pode ser omitido com segurança para comparações intervalares.


### Temporal (T) (Arthur Zanetti)
Valores *temporais* medem pontos ou intervalos no tempo. Esse tipo é um caso especial de valores quantitativos (carimbos de data/hora) com semânticas e convenções ricas (por exemplo, o [Calendário Gregoriano](https://en.wikipedia.org/wiki/Gregorian_calendar)). O tipo temporal no Vega-Lite suporta raciocínio sobre unidades de tempo (ano, mês, dia, hora, etc.) e oferece métodos para solicitar intervalos de tempo específicos.

Exemplos de valores temporais incluem strings de datas como <span style="color:deeppink">“2019-01-04”</span> e <span style="color:deeppink">"Jan 04 2019"</span> , bem como formatos padronizados de data e hora, como o [Formato ISO](https://en.wikipedia.org/wiki/ISO_8601): <span style="color:deeppink">“2019-01-04T17:50:35.643Z”</span>.

Não há valores temporais em nosso conjunto de dados de desenvolvimento global acima, já que o campo ano (<span style="color:deeppink">year</span>) é simplesmente codificado como um número inteiro. Para mais detalhes sobre o uso de dados temporais no Altair, consulte a documentação de [Horas e Datas](https://altair-viz.github.io/user_guide/times_and_dates.html).

### Resumo (Vinicius Prestes)

Estes tipos de dados não são mutuamente exclusivos. Na verdade, formam uma hierarquia: dados ordinais permitem comparação nominais (igualdades), enquanto dados quantitativos permitem comparações ordinais (ordenação).

Além disso, estes tipos de dados _não_ formam uma categorização única. Se um campo do dado é representado usando um número, isso não significa que devemos tratá-lo como um tipo quantitativo! Por exemplo, podemos interpretar um conjunto de idades (10 anos, 20 anos, etc) como um dado nominal (menor de idade ou maior de idade), ordinal (agrupado por ano), ou quantitativo (para o cálculo da média de idade).

Agora vamos analisar como codificar visualmente esses tipos de dados!

## Canais de Codificação (Vinicius Prestes)

A utilização de *codificações* que associam *campos de dados* (contendo dados de um certo tipo) com *canais* de codificação (de um tipo da *marca* escolhido) está no coração do Altair. Nesta seção, vamos examinar os seguintes canais de codificação:

- <span style="color:deeppink">x</span>: Posição horizontal (eixo x) da marca.
- <span style="color:deeppink">y</span>: Posição vertical (eixo y) da marca.
- <span style="color:deeppink">size</span>: Tamanho da marca. Pode se referir a uma área ou comprimento, dependendo do tipo da marca.
- <span style="color:deeppink">color</span>: Determina a cor da marca, especificado como uma [cor válida CSS](https://developer.mozilla.org/en-US/docs/Web/CSS/color_value).
- <span style="color:deeppink">opacity</span>: Determina a opacidade da marca, variando entre 0 (totalmente transparente) e 1 (totalmente opaco).
- <span style="color:deeppink">shape</span>: Determina o formato de marcas pontuais (<span style="color:deeppink">point</span>).
- <span style="color:deeppink">tooltip</span>: Informação textual a ser exibida ao passar o mouse sobre a marca.
- <span style="color:deeppink">order</span>: Determina a ordem. Estabelece a ordem de leitura e renderização de regiões da tela (linhas ou áreas).
- <span style="color:deeppink">column</span>: Organiza os dados em subgráficos alinhados horizontalmente.
- <span style="color:deeppink">row</span>: Organiza os dados em subgráficos alinhados verticalmente.

Veja a [documentação do Altair de codificação](https://altair-viz.github.io/user_guide/encoding.html) para uma lista completa dos canais disponíveis.

### X (Vinicius Prestes)

O canal de codificação <span style="color:deeppink">x</span> determina a posição horizontal de um marcador (coordenada x). Além disso, são feitas automaticamente escolhas padrão para os eixos e título (caso não especificados). No gráfico abaixo, a escolha de um dado quantitativo resulta em um eixo contínuo com escala linear:

In [8]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q')
)

alt.Chart(...)

### Y (Eliani)

O canal de codificação <span style="color:deeppink">y</span> define a posição vertical (coordenada y). Aqui nós adicionamos o campo grupo (<span style="color:deeppink">cluster</span>) usando um tipo de dados ordinal (<span style="color:deeppink">o</span>). O resultado é um eixo discreto que inclui uma faixa com tamanho de passo padrão, para cada valor único:

In [9]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q'),
    alt.Y('cluster:O')
)

alt.Chart(...)

_O que acontece com o gráfico acima se você trocar os tipos de campo <span style="color:deeppink">O</span> e <span style="color:deeppink">Q</span>?_

Se, em vez disso, adicionarmos o campo expectativa de vida (<span style="color:deeppink">life_expect</span>) como uma variável quantitativa (<span style="color:deeppink">Q</span>), o resultado será um gráfico de dispersão com escalas lineares para ambos os eixos:

In [10]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q')
)

alt.Chart(...)

Por padrão, os eixos para escalas quantitativas lineares incluem o zero para garantir uma linha de base adequada para a comparação de razões de valores de dados. Em alguns casos, no entanto, uma linha de base zero pode não fazer sentido ou pode querer concentrar-se em comparações de intervalos. Para desativar a inclusão automática do zero, configure o mapeamento da escala utilizando o atributo de codificação escala (<span style="color:deeppink">scale</span>):

In [11]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q', scale=alt.Scale(zero=False)),
    alt.Y('life_expect:Q', scale=alt.Scale(zero=False))
)

alt.Chart(...)

Agora, as escalas dos eixos já não incluem o zero por padrão. Algum preenchimento ainda permanece, já que os pontos finais do domínio do eixo são automaticamente ajustados para números _amistosos_ (_nice_) como múltiplos de 5 ou 10.

_O que acontece se você também adicionar <span style="color:deeppink">(nice=false)</span> ao atributo scale acima?_

### Tamanho (Eliani)

O canal de codificação tamanho (<span style="color:deeppink">size</span>) define o tamanho ou a extensão de uma marca. O significado do canal pode variar de acordo com o tipo de marca. Para marcas <span style="color:deeppink">ponto</span>, o canal <span style="color:deeppink">size</span> mapeia para a área de pixel do símbolo de plotagem, de forma que o diâmetro do ponto corresponda à raiz quadrada do valor do tamanho.

Vamos aumentar o nosso gráfico de dispersão codificando a população (<span style="color:deeppink">pop</span>) no canal <span style="color:deeppink">size</span>. Como resultado, o gráfico agora também inclui uma legenda para interpretar os valores de tamanho.

In [12]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q')
)

alt.Chart(...)

Em alguns casos, podemos não estar satisfeitos com a faixa de tamanho padrão. Para fornecer um intervalo personalizado de tamanhos, defina o parâmetro intervalo (<span style="color:deeppink">range</span>) do atributo de escala (<span style="color:deeppink">scale</span>) como um intervalo que indica o tamanho mínimo e máximo. Aqui atualizamos a codificação de tamanho para variar de 0 pixels (para valores zero) a 1.000 pixels (para o valor máximo no domínio da escala):

In [13]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000]))
)

alt.Chart(...)

### Cor e Opacidade (Eliani)

O canal de codificação cor (<span style="color:deeppink">color</span>) define a cor de uma marca. O estilo de codificação da cor é altamente dependente do tipo de dados: os dados nominais terão, por padrão, um esquema de cores qualitativo multi-colorido, enquanto os dados ordinais e quantitativos utilizarão gradientes de  uma cor perceptualmente ordenados.

Aqui, codificamos o campo grupo (<span style="color:deeppink">cluster</span>) usando o canal _color_ e um tipo de dados nominal (<span style="color:deeppink">N</span>), resultando em uma tonalidade distinta para cada valor do grupo. Consegue começar a adivinhar o que o campo <span style="color:deeppink">cluster</span> pode indicar?

In [14]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N')
)

alt.Chart(...)

Se preferirmos formas preenchidas, podemos passar um parâmetro <span style="color:deeppink">filled=true</span> para o método <span style="color:deeppink">mark_point</span>:

In [15]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N')
)

alt.Chart(...)

Por padrão, o Altair usa um pouco de transparência para ajudar a combater o excesso de plotagem. Podemos ajustar ainda mais a opacidade, seja passando um valor padrão para o método <span style="color:deeppink">mark_*</span>, ou usando um canal de codificação dedicado.

Aqui demonstramos como fornecer um valor constante a um canal de codificação em vez de vincular um campo de dados:

In [16]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N'),
    alt.OpacityValue(0.5)
)

alt.Chart(...)

### Formato (Joênio)

O canal de codificação formato (<span style="color:deeppink">shape</span>) define a forma geométrica usada pelos marcadores de <span style="color:deeppink">pontos</span>. Diferentemente dos outros canais que vimos até agora, o canal <span style="color:deeppink">shape</span> não pode ser usado por outros tipos de marca. O canal de codificação de forma deve ser usado apenas com dados nominais, pois comparações de ordem de classificação e magnitude perceptuais não são suportadas.

Vamos codificar o campo grupo (<span style="color:deeppink">cluster</span>) usando formato (<span style="color:deeppink">shape</span>), assim como cor (<span style="color:deeppink">color</span>). Usar vários canais para o mesmo campo de dados subjacente é conhecido como uma codificação redundante. O gráfico resultante combina informações de cor e forma em uma única legenda de símbolo:

In [17]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N'),
    alt.OpacityValue(0.5),
    alt.Shape('cluster:N')
)

alt.Chart(...)

### Dicas de ferramentas e ordenação (Joênio)

A essa altura, você pode se sentir um pouco frustrado: nós construímos um gráfico, mas ainda não sabemos a quais países os pontos visualizados correspondem! Vamos adicionar dicas de ferramentas interativas para permitir a exploração.

O canal de codificação de dicas de ferramenta (<span style="color:deeppink">tooltip</span>) determina o texto da dica de ferramenta a ser exibido quando um usuário move o cursos do mouse sobre uma marca. Vamos adicionar uma codificação de dica de ferramenta para o campo país (<span style="color:deeppink">country</span>) e, em seguida, investigar quais países estão sendo representados.

In [18]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N'),
    alt.OpacityValue(0.5),
    alt.Tooltip('country')
)

alt.Chart(...)

Conforme você passa o mouse, pode perceber que não consegue selecionar alguns pontos. Por exemplo, o maior círculo azul escuro corresponde a Índia, que é desenhado em cima de um país como uma população menor, impedindo que o mouse passe sobre esse país. Para corrigir esse problema, podemos usar o canal de codificação ordem (<span style="color:deeppink">order</span>).

O canal de codificação <span style="color:deeppink">order</span> determina a ordem dos pontos de dados, afetando tanto a ordem em que são desenhados quanto, para marcas linha (<span style="color:deeppink">line</span>) e área (<span style="color:deeppink">area</span>), a ordem em que são conectados uns aos outros.

Vamos ordenar os valores em ordem decrescente de classificação pela população (<span style="color:deeppink">pop</span>), garantindo que os círculos menores sejam desenhados depois dos círculos maiores:

In [19]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N'),
    alt.OpacityValue(0.5),
    alt.Tooltip('country:N'),
    alt.Order('pop:Q', sort='descending')
)

alt.Chart(...)

Agora podemos identificar o país menor que está sendo obscurecido pela Índia: é Bangladesh!

Agora também podemos descobrir o que o campo grupo (<span style="color:deeppink">cluster</span>) representa. Passe o mouse sobre os vários pontos coloridos para formular sua própria explicação.

Neste ponto, adicionamos dicas de ferramentas que mostram apenas uma única propriedade do registro de dados subjacente. Para mostrar vários valores, podemos fornecer ao canal <span style="color:deeppink">tooltip</span> um array de codificações, uma para cada campo que queremos incluir: 

In [20]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N'),
    alt.OpacityValue(0.5),
    alt.Order('pop:Q', sort='descending'),
    tooltip = [
        alt.Tooltip('country:N'),
        alt.Tooltip('fertility:Q'),
        alt.Tooltip('life_expect:Q')
    ]   
)

alt.Chart(...)

Agora podemos ver vários campos de dados ao passar o mouse!

<!--### Column and Row Facets-->

### Facetas de colunas e linhas (Erique)

<!--Spatial position is one of the most powerful and flexible channels for visual encoding, but what can we do if we already have assigned fields to the `x` and `y` channels? One valuable technique is to create a *trellis plot*, consisting of sub-plots that show a subset of the data. A trellis plot is one example of the more general technique of presenting data using [small multiples](https://en.wikipedia.org/wiki/Small_multiple) of views.

The `column` and `row` encoding channels generate either a horizontal (columns) or vertical (rows) set of sub-plots, in which the data is partitioned according to the provided data field.

Here is a trellis plot that divides the data into one column per \`cluster\` value:-->

<!--

    Algumas correções de tradução.

    Gráfico de Treliças -> Painel em grade
-->


A posição espacial é um dos tópicos mais poderosos e flexíveis para codificação visual de dados, mas o que podemos fazer se já atribuímos campos aos canais <span style="color:deeppink">x</span> e <span style="color:deeppink">y</span>? Uma técnica valiosa é criar um *painel em grade*, que consiste em subgráficos que mostram um subconjunto dos dados. Um painel em grade é um exemplo da técnica mais geral de apresentação de dados usando pequenos múltiplos ([Small multiple](https://en.wikipedia.org/wiki/Small_multiple)) de visualizações.

Os canais de codificação de coluna (<span style="color:deeppink">column</span>) e de linha (<span style="color:deeppink">line</span>) geram um conjunto horizontal (colunas) ou vertical (linhas) de subparcelas, nas quais os dados são particionados de acordo com o campo de dados fornecido.

Aqui está um painel em grade que divide os dados em uma coluna por valor de grupo (<span style="color:deeppink">cluster</span>):

In [21]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000])),
    alt.Color('cluster:N'),
    alt.OpacityValue(0.5),
    alt.Tooltip('country:N'),
    alt.Order('pop:Q', sort='descending'),
    alt.Column('cluster:N')
)

alt.Chart(...)

<!--The plot above does not fit on screen, making it difficult to compare all the sub-plots to each other! We can set the default `width` and `height` properties to create a smaller set of multiples. Also, as the column headers already label the `cluster` values, let's remove our `color` legend by setting it to `None`. To make better use of space we can also orient our `size` legend to the `'bottom'` of the chart.-->

A totalidade dos dados acima não cabe na tela, dificultando a comparação de todas as unidades gráficas entre si! Podemos definir as propriedades padrão  largura (<span style="color:deeppink">width</span>) e altura (<span style="color:deeppink">height</span>) para criar um conjunto menor de múltiplos. Além disso, como os cabeçalhos das colunas já rotulam os valores de grupo (<span style="color:deeppink">cluster</span>), vamos remover nossa legenda de cor (<span style="color:deeppink">color</span>) definindo-a como <span style="color:deeppink">None</span>. Para aproveitar melhor o espaço também podemos orientar nossa legenda de tamanho (<span style="color:deeppink">size</span>) para a parte inferior (<span style="color:deeppink">bottom</span>) do gráfico.

In [22]:
alt.Chart(data2000).mark_point(filled=True).encode(
    alt.X('fertility:Q'),
    alt.Y('life_expect:Q'),
    alt.Size('pop:Q', scale=alt.Scale(range=[0,1000]),
             legend=alt.Legend(orient='bottom', titleOrient='left')),
    alt.Color('cluster:N', legend=None),
    alt.OpacityValue(0.5),
    alt.Tooltip('country:N'),
    alt.Order('pop:Q', sort='descending'),
    alt.Column('cluster:N')
).properties(width=135, height=135)

alt.Chart(...)

<!--Underneath the hood, the `column` and `row` encodings are translated into a new specification that uses the `facet` view composition operator. We will re-visit faceting in greater depth later on!

In the meantime, _can you rewrite the chart above to facet into rows instead of columns?_-->

Implicitamente, as codificações <span style="color:deeppink">column</span> e <span style="color:deeppink">row</span> são traduzidas em uma nova especificação que usa o operador de composição de visualização faceta (<span style="color:deeppink">facet</span>). Iremos revisitar o facetamento com maior profundidade mais tarde!

Enquanto isso, _você consegue reescrever o gráfico acima para dividi-lo em linhas em vez de colunas?_

<!--### A Peek Ahead: Interactive Filtering

In later modules, we'll dive into interaction techniques for data exploration. Here is a sneak peak: binding a range slider to the `year` field to enable interactive scrubbing through each year of data. Don't worry if the code below is a bit confusing at this point, as we will cover interaction in detail later.

_Drag the slider back and forth to see how the data values change over time!_-->

### Uma prévia: filtragem interativa (Erique)

Nos módulos posteriores, nos aprofundaremos nas técnicas de interação para exploração de dados. Aqui está uma prévia: vincular um controle deslizante de intervalo ao campo ano (<span style="color:deeppink">year</span>) para permitir a limpeza interativa de cada ano de dados. Não se preocupe se o código abaixo estiver um pouco confuso neste momento, pois abordaremos a interação em detalhes posteriormente.

_Arraste o controle deslizante para frente e para trás para ver como os valores dos dados mudam ao longo do tempo!_



In [23]:
select_year = alt.selection_point(
    name='select',
    fields=['year'],
    value={'year': 1955},
    bind=alt.binding_range(min=1955, max=2005, step=5)
)

chart = alt.Chart(data).mark_point(filled=True).encode(
    alt.X('fertility:Q', scale=alt.Scale(domain=[0, 9])),
    alt.Y('life_expect:Q', scale=alt.Scale(domain=[0, 90])),
    alt.Size('pop:Q', scale=alt.Scale(domain=[0, 1200000000], range=[0, 1000])),
    alt.Color('cluster:N', legend=None),
    alt.OpacityValue(0.5),
    alt.Tooltip('country:N'),
    alt.Order('pop:Q', sort='descending')
).add_params(
    select_year
).transform_filter(
    select_year
)
chart

alt.Chart(...)

<!--## Graphical Marks

Our exploration of encoding channels above exclusively uses `point` marks to visualize the data. However, the `point` mark type is only one of the many geometric shapes that can be used to visually represent data. Altair includes a number of built-in mark types, including:

- `mark_area()` - Filled areas defined by a top-line and a baseline.
- `mark_bar()` -	Rectangular bars.
- `mark_circle()`	- Scatter plot points as filled circles.
- `mark_line()` - Connected line segments.
- `mark_point()` - Scatter plot points with configurable shapes.
- `mark_rect()` - Filled rectangles, useful for heatmaps.
- `mark_rule()` - Vertical or horizontal lines spanning the axis.
- `mark_square()` - Scatter plot points as filled squares.
- `mark_text()` - Scatter plot points represented by text.
- `mark_tick()` - Vertical or horizontal tick marks.	

For a complete list, and links to examples, see the [Altair marks documentation](https://altair-viz.github.io/user_guide/marks.html). Next, we will step through a number of the most commonly used mark types for statistical graphics.-->

## Marcas Gráficas (Erique)

Nossa exploração dos canais de codificação acima usa exclusivamente marcas do tipo ponto (<span style="color:deeppink">point</span>) para visualizar os dados. No entanto, o tipo de marca de ponto é apenas uma das muitas formas geométricas que podem ser usadas para representar dados visualmente. Altair inclui vários tipos de marcas integradas, incluindo:

- <span style="color:deeppink">mark_area()</span> - Áreas preenchidas definidas por uma linha superior e uma linha de base.
-  <span style="color:deeppink">mark_bar()</span> - Barras retangulares.
-  <span style="color:deeppink">mark_circle()</span> - Disperse os pontos do gráfico como círculos preenchidos.
-  <span style="color:deeppink">mark_line()</span> - Segmentos de linha conectados.
-  <span style="color:deeppink">mark_point()</span> - Disperse pontos do gráfico com formas configuráveis.
-  <span style="color:deeppink">mark_rect()</span> - Retângulos preenchidos, úteis para mapas de calor.
-  <span style="color:deeppink">mark_rule()</span> - Linhas verticais ou horizontais que abrangem o eixo.
-  <span style="color:deeppink">mark_square()</span> - Disperse os pontos do gráfico como quadrados preenchidos.
-  <span style="color:deeppink">mark_text()</span> - Pontos do gráfico de dispersão representados por texto.
-  <span style="color:deeppink">mark_tick()</span> - Marcas verticais ou horizontais.	

Para obter uma lista completa e links para exemplos, consulte a [documentação de marcas do Altair](https://altair-viz.github.io/user_guide/marks.html). A seguir, examinaremos alguns dos tipos de marcas mais comumente usados ​​para gráficos estatísticos.

### Marca de Ponto (Pedro Henrique Barbosa)

O tipo marca de ponto (<span style="color:deeppink">point</span>) é utilizado para representar pontos específicos, como em gráficos de dispersão e gráficos de pontos. Além dos canais de codificação <span style="color:deeppink">x</span> e <span style="color:deeppink">y</span> (para especificar posições de pontos 2D), as marcas de ponto podem usar codificações de <span style="color:deeppink">color</span>,  <span style="color:deeppink">size</span> e <span style="color:deeppink">shape</span> para transmitir campos de dados adicionais.

Segue um gráfico de pontos da fecundidade (<span style="color:deeppink">fertility</span>), com o campo de grupo (<span style="color:deeppink">cluster</span>) codificado de forma redundante utilizando os canais <span style="color:deeppink">y</span> e de forma (<span style="color:deeppink">shape</span>).
 

In [24]:
alt.Chart(data2000).mark_point().encode(
    alt.X('fertility:Q'), # fecundidade
    alt.Y('cluster:N'), # grupo
    alt.Shape('cluster:N') 
) 

alt.Chart(...)

Para além dos canais de codificação, as marcas podem ser estilizadas, basta fornecermos valores aos métodos <span style="color:deeppink">mark_*()</span>.

Por exemplo: as marcas de pontos são desenhadas com contornos traçados por predefinição, mas podem ser especificadas para utilizar formas preenchidas (<span style="color:deeppink">filled</span>). Da mesma forma, é possível predefinir um tamanho (<span style="color:deeppink">size</span>) para área total de pixels da marca de ponto.

In [25]:
alt.Chart(data2000).mark_point(filled=True, size=100).encode(
    alt.X('fertility:Q'), # Fecundidade
    alt.Y('cluster:N'), # Grupo
    alt.Shape('cluster:N') 
)

alt.Chart(...)

### Marca de Círculo (Pedro Henrique Barbosa)

O tipo marca de círculo (<span style="color:deeppink">circle</span>) é uma categoria conveniente para as marcas de ponto na forma de círculos preenchidos.

In [26]:
alt.Chart(data2000).mark_circle(size=100).encode(
    alt.X('fertility:Q'), # Fecundidade
    alt.Y('cluster:N'), # Grupo
    alt.Shape('cluster:N')
)

alt.Chart(...)

### Marca de Quadrado (Pedro Henrique Barbosa)

O tipo marca de quadrado (<span style="color:deeppink">square</span>) é uma categoria conveniente para as marcas de ponto na forma de quadrados preenchidos.

In [27]:
alt.Chart(data2000).mark_square(size=100).encode(
    alt.X('fertility:Q'), # Fecundidade
    alt.Y('cluster:N'), # Grupo
    alt.Shape('cluster:N')
)

alt.Chart(...)

### Marca de Traço (Pedro Henrique Barbosa)

O tipo marca de traço (<span style="color:deeppink">tick</span>) transmite um ponto de dados utilizando um segmento de linha curto ou "tick". Estes são particularmente úteis para comparar valores ao longo de uma única dimensão com uma sobreposição mínima. Um gráfico de pontos desenhado com marcas de traço é por vezes referido como um *strip plot*.

In [28]:
alt.Chart(data2000).mark_tick().encode(
    alt.X('fertility:Q'), # Fecundidade
    alt.Y('cluster:N'), # Grupo
    alt.Shape('cluster:N')
)

alt.Chart(...)

### Marcas de barra (Tainá)

O tipo marca de barra (<span style="color:deeppink">bar</span>) desenha um retângulo com uma posição, largura e altura.

O gráfico abaixo é um gráfico de barras simples da população (<span style="color:deeppink">pop</span>) de cada país.

In [29]:
alt.Chart(data2000).mark_bar().encode(
    alt.X('country:N', title='País'),
    alt.Y('pop:Q', title='População')
)

alt.Chart(...)

A largura das barras é definida com um tamanho padrão. Discutiremos como ajustar a largura das barras mais adiante neste caderno. (Um caderno subsequente analisará mais de perto a configuração de eixos, escalas e legendas.)

As barras também podem ser empilhadas. Vamos alterar a codificação do eixo <span style="color:deeppink">x</span> para usar o campo de grupo (<span style="color:deeppink">cluster</span>) e codificar um país (<span style="color:deeppink">country</span>) utilizando o canal de cor (<span style="color:deeppink">color</span>). Também desativaremos a legenda (que seria muito longa com cores para todos os países!) e usaremos dicas de ferramenta (<span style="color:deeppink">tooltips</span>) para o nome do país.

In [30]:
alt.Chart(data2000).mark_bar().encode(
    alt.X('cluster:N', title='Grupo'),
    alt.Y('pop:Q', title='População'),
    alt.Color('country:N', legend=None),
    alt.Tooltip('country:N')
)

alt.Chart(...)

No gráfico acima, o uso do canal de codificação de (<span style="color:deeppink">color</span>) faz com que o Altair / Vega-Lite empilhe automaticamente as marcas de barras. Caso contrário, as barras seriam desenhadas uma sobre a outra! Tente adicionar o parâmetro <span style="color:deeppink">stack=None</span> ao canal de codificação <span style="color:deeppink">y</span> para ver o que acontece se não aplicarmos o empilhamento...

Os exemplos acima criam gráficos de barras com a base partindo do zero, e o canal <span style="color:deeppink">y</span> codifica apenas a altura da barra. No entanto, a marca de barra também permite especificar pontos de início e fim para representar intervalos.

O gráfico abaixo usa os canais <span style="color:deeppink">x</span> (ponto de início) e <span style="color:deeppink">x2</span> (ponto de fim) para mostrar o intervalo de expectativa de vida dentro de cada grupo (<span style="color:deeppink">cluster</span>) regional. Abaixo, usamos as funções de agregação mínimo (<span style="color:deeppink">min</span>) e máximo (<span style="color:deeppink">max</span>) para determinar os pontos extremos do intervalo; discutiremos a agregação em mais detalhes no próximo _notebook_!

Alternativamente, você pode usar <span style="color:deeppink">x</span> e largura (<span style="color:deeppink">width</span>) para fornecer um ponto de início mais um deslocamento, de forma que <span style="color:deeppink">x2 = x + width</span>.

In [31]:
alt.Chart(data2000).mark_bar().encode(
    alt.X('min(life_expect):Q', title='Mínimo de expectativa de vida'),
    alt.X2('max(life_expect):Q', title='Máximo de expectativa de vida'),
    alt.Y('cluster:N', title='Grupo')
)

alt.Chart(...)

### Marcas de linha (Tainá)

O tipo de marca de linha (<span style="color:deeppink">line</span>) conecta os pontos plotados com segmentos de linha para que, por exemplo, a inclinação da linha transmita informações sobre a taxa de variação.

Vamos exibir um gráfico de linha da fecundidade por país ao longo dos anos, usando o _data frame_ de desenvolvimento global. Novamente, vamos substituir a legenda por <span style="color:deeppink">_tooltips_</span>.

In [32]:
alt.Chart(data).mark_line().encode(
    alt.X('year:O', title='Ano'),
    alt.Y('fertility:Q', title='Fecundidade'),
    alt.Color('country:N', legend=None),
    alt.Tooltip('country:N')
).properties(
    width=400
)

alt.Chart(...)


Podemos observar variações interessantes por país e tendências gerais de menores números de filhos por família ao longo do tempo. Também vale notar que definimos uma largura personalizada de 400 pixels. _Tente alterar (ou remover) as larguras e veja o que acontece!_

Vamos alterar alguns dos parâmetros padrão da marca para personalizar o gráfico. Podemos definir a largura do traço (<span style="color:deeppink">strokeWidth</span>) para determinar a espessura das linhas e a opacidade (<span style="color:deeppink">opacity</span>) para adicionar transparência. Por padrão, a marca  de linha (<span style="color:deeppink">line</span>) usa segmentos de linha reta para conectar os pontos de dados. Em alguns casos, podemos querer suavizar as linhas. Podemos ajustar a interpolação usada para conectar os pontos de dados configurando o parâmetro interpolação de marca (<span style="color:deeppink">interpolate</span>). Vamos usar a interpolação monótona (<span style="color:deeppink">monotone</span>) para fornecer linhas suaves que também garantem que não sejam gerados "falsos" valores mínimos ou máximos como resultado da interpolação.

In [33]:
alt.Chart(data).mark_line(
    strokeWidth=3,
    opacity=0.5,
    interpolate='monotone'
).encode(
    alt.X('year:O', title='Ano'),
    alt.Y('fertility:Q', title='Fecundidade'),
    alt.Color('country:N', legend=None),
    alt.Tooltip('country:N')
).properties(
    width=400
)

alt.Chart(...)


A marca de <span style="color:deeppink">linha</span> também pode ser usada para criar *gráficos de inclinação* (slope graphs), ou seja, gráficos que destacam a mudança de valor entre dois pontos de comparação usando a inclinação das linhas.

Abaixo, vamos criar um gráfico de inclinação comparando as populações de cada país nos anos mínimo e máximo de nosso conjunto de dados: 1955 e 2005. Primeiro, criamos um novo _data frame_ do Pandas filtrado para esses anos e, em seguida, usamos o Altair para criar o gráfico de inclinação.

Por padrão, o Altair coloca os anos próximos uns dos outros. Para espaçar melhor os anos ao longo do eixo x, podemos indicar o tamanho (em pixels) dos passos discretos ao longo da largura do nosso gráfico, conforme indicado no comentário abaixo. Tente ajustar o valor de <span style="color:deeppink">step</span> abaixo e veja como o gráfico muda em resposta.

In [34]:
dataTime = data.loc[(data['year'] == 1955) | (data['year'] == 2005)]

alt.Chart(dataTime).mark_line(opacity=0.5).encode(
    alt.X('year:O', title='Ano'),
    alt.Y('pop:Q', title='População'),
    alt.Color('country:N', legend=None),
    alt.Tooltip('country:N')
).properties(
    width={"step": 50} # ajusta o parâmetro de passos
)

alt.Chart(...)

### 2.4.7. Marcas de Área (David Farina)
A marca do tipo área (<span style="color:deeppink">area</span>) combina alguns aspectos da marca de linha (<span style="color:deeppink">line</span>) e de barra (<span style="color:deeppink">bar</span>): ela encontra conexões entre os pontos dos dados, e também exibe uma região preenchida, com uma borda correspondente a uma linha de base com valor nulo.


O gráfico abaixo é um gráfico de área com dados da população sobre o tempo dos Estados Unidos.

In [35]:
dataUS = data.loc[data['country'] == 'United States']

alt.Chart(dataUS).mark_area().encode(
    alt.X('year:O'),
    alt.Y('fertility:Q')
)

alt.Chart(...)

Similarmente às marcas de linha, marcas de área  contam com um parâmetro de interpolação (<span style="color:deeppink">interpolate</span>).

In [36]:
alt.Chart(dataUS).mark_area(interpolate='monotone').encode(
    alt.X('year:O'),
    alt.Y('fertility:Q')
)

alt.Chart(...)

Assim como marcas de barra, marcas de área também permitem o empilhamento (stacking). Aqui nós criamos um novo _data frame_ com os dados para os três países norte americanos e os plotamos utilizando a marca de área e um canal que indica a cor (<span style="color:deeppink">color</span>) para empilhar considerando o país.

In [37]:
dataNA = data.loc[
    (data['country'] == 'United States') |
    (data['country'] == 'Canada') |
    (data['country'] == 'Mexico')
]

alt.Chart(dataNA).mark_area().encode(
    alt.X('year:O'),
    alt.Y('pop:Q'),
    alt.Color('country:N')
)

alt.Chart(...)

Por padrão, o _stacking_ é feito considerando uma linha de base nula, entretanto, temos outras opções disponíveis para fazê-lo:
- <span style="color:deeppink">center</span> - para empilhar em relação a uma linha de base no centro do gráfico, criando uma visualização como um gráfico de fluxo, e também
- <span style="color:deeppink">normalize</span> - para normalizar os dados como um todo em relação a 100%, assim, tornando possível comparações por porcentagem.


Abaixo, nós adaptamos o gráfico associando ao parâmetro <span style="color:deeppink">stack</span> no eixo <span style="color:deeppink">y</span>, o atributo <span style="color:deeppink">center</span>. O que aconteceria se colocássemos <span style="color:deeppink">normalize</span> ao invés de <span style="color:deeppink">center</span> no parâmetro?

In [38]:
alt.Chart(dataNA).mark_area().encode(
    alt.X('year:O'),
    alt.Y('pop:Q', stack='center'),
    alt.Color('country:N')
)

alt.Chart(...)

Para desativar o stacking completamente, é necessário colocar o atributo do <span style="color:deeppink">stack</span> como <span style="color:deeppink">None</span>. Nós podemos também adicionar <span style="color:deeppink">opacity</span> como um parâmetro de marca padrão para assegurar que veremos as áreas de sobreposição!

In [39]:
alt.Chart(dataNA).mark_area(opacity=0.5).encode(
    alt.X('year:O'),
    alt.Y('pop:Q', stack=None),
    alt.Color('country:N')
)

alt.Chart(...)

A marca de área também aceita linhas de base de dados direcionados, com ambas, séries superiores e inferiores determinadas pelo domínio dos dados. Assim como com marcas de barra, podemos usar os canais <span style="color:deeppink">x</span> e <span style="color:deeppink">x2</span> (ou <span style="color:deeppink">y</span> e <span style="color:deeppink">y2</span>) para obter pontos finais para as marcas de área.

O gráfico abaixo é uma visualização do intervalo de fecundidade máxima e mínima por ano para os países Norte Americanos:

In [40]:
alt.Chart(dataNA).mark_area().encode(
    alt.X('year:O'),
    alt.Y('min(fertility):Q'),
    alt.Y2('max(fertility):Q')
).properties(
    width={"step": 40}
)

alt.Chart(...)

Podemos notar um maior intervalo de valores em 1995, de logo abaixo de 4 até logo abaixo de 7. Por volta de 2005, ambos os valores de fecundidade e variabilidade total tiveram uma queda, centrados em torno de 2 crianças por família.


Todos os exemplos de marca de área usados acima, usam um área verticalmente orientada. Entretanto, o Altair e o Vega-Lite também permitem áreas horizontais. Vamos transpor o gráfico acima simplesmente trocando os canais <span style="color:deeppink">x</span> e <span style="color:deeppink">y</span>

In [41]:
alt.Chart(dataNA).mark_area().encode(
    alt.Y('year:O'),
    alt.X('min(fertility):Q'),
    alt.X2('max(fertility):Q')
).properties(
    width={"step": 40}
)

alt.Chart(...)

## Resumo (Armando)

Concluímos nossa introdução aos tipos de dados, canais de codificação e marcas gráficas! Agora você deve estar bem preparado para explorar mais a fundo o espaço de codificações, tipos de marcas e parâmetros de marcas. Para uma referência abrangente – incluindo recursos que não abordamos aqui – consulte a documentação de [marcas](https://altair-viz.github.io/user_guide/marks.html) e [codificação](https://altair-viz.github.io/user_guide/encoding.html) do Altair.

No próximo módulo, veremos o uso de transformações de dados para criar gráficos que resumem dados ou visualizam novos campos derivados. Em um módulo futuro, examinaremos como personalizar ainda mais seus gráficos modificando escalas, eixos e legendas.

Interessado em aprender mais sobre codificação visual?


![Texto alternativo](Imagens\cap2_section2.5_graf1.png)

### Taxonomia de codificações visuais de Bertin, adaptada de [*Sémiologie Graphique*](https://books.google.com.br/books/about/Semiology_of_Graphics.html?id=X5caQwAACAAJ&redir_esc=y) por [Mike Bostock](https://bost.ocks.org/mike/).

- O estudo sistemático de marcas, codificações visuais e tipos de dados associados foi iniciado por [Jacques Bertin](https://en.wikipedia.org/wiki/Jacques_Bertin) em sua obra pioneira de 1967 [*Sémiologie Graphique (A Semiologia dos Gráficos)*](https://books.google.com.br/books/about/Semiology_of_Graphics.html?id=X5caQwAACAAJ&redir_esc=y). A imagem acima ilustra canais como posição, tamanho, valor (brilho), textura, cor (matiz), orientação e forma, juntamente com as recomendações de Bertin para os tipos de dados que eles suportam.

- A estrutura de tipos de dados, marcas e canais também orienta ferramentas automatizadas de design de visualizações, começando com a [APT (A Presentation Tool)](https://scholar.google.com/scholar?cluster=10191273548472217907) de Mackinlay em 1986 e continuando em sistemas mais recentes, como o [Voyager](https://idl.uw.edu/papers/voyager) e o [Draco](https://idl.uw.edu/papers/draco).

- A identificação de tipos de dados nominais, ordinais, intervalares e de razão remonta pelo menos ao artigo de 1947 de S. S. Stevens, [*On the theory of scales of measurement*](https://scholar.google.com/scholar?cluster=14356809180080326415).


## Exemplos

E desta forma encerramos o capítulo 2. Segue exemplos feitos pelo grupo utilizando da biblioteca altair.

In [42]:
from vega_datasets import data

### Exemplo 1.1 (Armando): Stocks (Ações)
Se trata de uma apresentação gráfica do conjunto de dados chamado `stocks` da biblioteca `vega_datasets`. Esse conjunto guarda informações sobre a evolução do preço de três ações, são elas: **AAPL**(Apple), **AMZN**(Amazon), **GOOG**(Google), **IBM**(IBM) e **MSFT**(Microsoft). O objetivo da visualização foi descrever a evolução dessas grandes empresas a partir do valor de suas ações ao longo do tempo. Para melhor visualização, foi usado apenas o ano da variável `date` no eixo ***x***.

In [43]:
# Carregar os dados
stocks = data.stocks()

# Criar o gráfico melhorado
chart = alt.Chart(stocks).mark_line(
    strokeWidth=5
).encode(
    alt.X('date:T', title='Data', axis=alt.Axis(format='%Y', labelAngle=-45)),  # Formatar eixo X
    alt.Y('price:Q', title='Preço'),
    alt.Color('symbol:N', title='Símbolo da Ação'),  # Adicionar legenda com título
    tooltip=['symbol:N','date:T', 'price:Q']  
).properties(
    width=600,  # Ajustar a largura
    height=400  # Ajustar a altura
).configure_axis(
    grid=False  # Remover linhas de grade (opcional)
)

chart



alt.Chart(...)

### Exemplo 1.2 (Armando): Crimea
Esse gráfico foi feito usando a base de dados chamada `crimea` em que são reportados os números de mortes em cada dia do mês, as mortes são separadas em variáveis que as classificam de acordo com sua causa, sendo elas: **ferimentos**, **doenças** e **outros**. Para construção do gráfico, as mortes foram agrupadas em uma única variável e os registros foram agrupados pelo mês do ano correspondente. O objetivo era visualizar a evolução do número de mortos. Percebe-se que houve um aumento no número de mortes nesse período e logo após houve uma diminuição. Isso reflete o evento de guerra corrente nesse período.

In [44]:
# Carregar os dados da Crimeia
crimea = data.crimea()

crimea['total_deaths'] = crimea['wounds'] + crimea['other'] + crimea['disease']
crimea['month_short'] = crimea['date'].dt.strftime('%Y-%m')


chart = alt.Chart(crimea).mark_bar().encode(
    alt.X('month_short:O', title='Data'),  # Formatar eixo X
    alt.Y('total_deaths:Q', title='Mortes'),
    tooltip = ['total_deaths'] 
).properties(
    width=900,  # Ajustar a largura
    height=600  # Ajustar a altura
)

chart




alt.Chart(...)

### Exemplo 2 (David): Mortes por desastres naturais

Aqui vamos observar como se deram as mortes devido a desastres naturais, sejam eles de origem geológica, devido a presença do humano na natureza, entre outros fatores que consideraremos como "naturais".

Agora, nos basta definir nossa base de dados como a base `disaster`, para então podermos trabalhar com ela.

In [45]:
disaster = data.disasters()
disaster.head()

Entity  Year   Deaths
0  All natural disasters  1900  1267360
1  All natural disasters  1901   200018
2  All natural disasters  1902    46037
3  All natural disasters  1903     6506
4  All natural disasters  1905    22758

Agora, partindo dessa nossa base de dados, definiremos dois diferentes Datasets. Para o primeiro, consideraremos apenas os desastres naturais sem contar o dado que considera as informações totais daquele ano quanto aos desastres. Já para o segundo, queremos apenas o dado que indica o valor total de todos os desastres

In [46]:
# Dataset desconsiderando o dado de todos os desastres
allnatural = disaster[disaster['Entity']!='All natural disasters']

# Dataset apenas com o dado de todos os desastres
every = disaster[disaster['Entity']=='All natural disasters']

'''
seca = disaster[disaster['Entity']=='Drought']
terrem = disaster[disaster['Entity']=='Earthquake']
empidem = disaster[disaster['Entity']=='Epidemic']
temp = disaster[disaster['Entity']=='Extreme temperature']
weather = disaster[disaster['Entity']=='Extreme weather']
enchen = disaster[disaster['Entity']=='Flood']
deslize = disaster[disaster['Entity']=='Landslide']
massa = disaster[disaster['Entity']=='Mass movement (dry)']
vulcao = disaster[disaster['Entity']=='Volcanic activity']
floresta = disaster[disaster['Entity']=='Wildfire']
'''

print(every.head(),'\n')

print(allnatural)



                  Entity  Year   Deaths
0  All natural disasters  1900  1267360
1  All natural disasters  1901   200018
2  All natural disasters  1902    46037
3  All natural disasters  1903     6506
4  All natural disasters  1905    22758 

       Entity  Year   Deaths
117   Drought  1900  1261000
118   Drought  1910    85000
119   Drought  1920   524000
120   Drought  1921  1200000
121   Drought  1928  3000000
..        ...   ...      ...
798  Wildfire  2013       35
799  Wildfire  2014       16
800  Wildfire  2015       67
801  Wildfire  2016       39
802  Wildfire  2017       75

[686 rows x 3 columns]


Para a nossa análise dos dados, primeiro vamos considerar os dados individuais dos desastres naturais.

Nosso objetivo aqui será observar como se dará a variação de mortes por ano considerando os desastres separadamente, para podemos entender como seu a proporcionalidade de mortes a cada ano. Além disso, podemos utilizar a visualização para entender as razões que levaram aos dados a ser de determinada maneira em certo ano ou período.

Apesar das considerações anteriores, primeiro precisamos fazer uma pequena alteração em nossos dados, para que não tenha espaços vazios em nenhum ano para nenhum dado. Para isso faremos o seguinte:

In [47]:
# Determinando qual será o intervalo de anos em que queremos preencher os dados
years = range(allnatural['Year'].min(), allnatural['Year'].max() + 1)

# Consideramos apenas um elemento de cada
elements = allnatural['Entity'].unique()

# Fazemos um novo Dataframe, mas com que todas as entidades tenham todos os anos em  seus dados
full_grid = pd.DataFrame([(year, elem) for year in years for elem in elements], 
                         columns=['Year', 'Entity'])

# Juntamos o Dataframe criado com o que ja tínhamos, preenchendo assim as lacunas faltantes de dados
complete_data = pd.merge(full_grid, allnatural, on=['Year', 'Entity'], how='left')

# Para termos uma melhor visualização, definimos todos os valores Nan como 0
complete_data["Deaths"] = complete_data['Deaths'].fillna(0)




Com nossos dados completos, agora podemos fazer uma visualização que nos ajudará a entender melhor quais desastres naturais afetaram mais cada ano.

In [48]:
# Como queremos faer uma visualização para que seja possível vermos os dados a cada ano, precisamos de uma barra deslizante.
select_year = alt.selection_point(
    name='Select',
    fields=['Year'],
    value = 1900,
    init={'Year':1900},
    bind=alt.binding_range(min=1900, max=2017, step=1)
)

# Aqui, fazemos o gráfico (com os dados completos), para podermos visualizar corretamente os dados em cad ano
entity_chart = alt.Chart(complete_data).mark_bar().encode(
    alt.X("Deaths:Q"),
    alt.Y("Entity:N"),
    alt.Color('Entity:N', legend=None),
    alt.Tooltip('Entity:N')
).add_params(select_year).transform_filter(select_year).properties(
    width=400,
    height= 200
)
entity_chart

alt.Chart(...)

Com o gráfico feito, podemos observar o comportamento por ano dos desastres naturais individualmente.

Agora, para uma segunda visualização, vamos observar como se deu em sua totalidade a variação nas mortes a cada ano. Para isso, faremos duas visualizações diferentes, uma que nos permitirá ver as variações ano a ano, que acompanha o gráfico anterior, e outra que nos mostra esse comportamento de maneira estática, pra termos uma noção um pouco melhor da amplitude dessas variações.

Para fazermos isso, entes precisamos definir uma nova coluna em nossos dados, essa coluna representará a variação ano a ano no total de mortes. Para conseguirmos fazer isso, vamos usar a função `pct_change()`, que calcula a variação percentual entre elementos consecutivos num Dataframe.

In [ ]:
every['variation'] =every['Deaths'].pct_change()
every['variation'] =every['variation'].fillna(0)

every.head()


Com esses novos dados, agora podemos simplesemente fazer o gráfico assim como o anterior.

In [50]:
# Determinando como será a barra de deslizamento
year_selection = alt.selection_point(
    name='Select',
    fields=['Year'],
    value = 1900,
    init={'Year':1900},
    bind=alt.binding_range(min=1900, max=2017, step=1)
)

# Faremos um gráfico com marca de ponto pois é a que demonstra uma maneira mais fácil para vermos o comportamento ao longo do tempo
total_chart = alt.Chart(every).mark_point().encode(
    x=alt.X('Year:Q', title='Ano', scale=alt.Scale(domain=[1900, 2017])), 
    y=alt.Y('variation:Q', title='Variação total', scale=alt.Scale(domain=[-0.9972122154018693, 8410.69])),  
    color=alt.Color('Entity:N', legend=alt.Legend(title='Entidade')),  
    tooltip=['Year', 'variation', 'Entity']  
).add_params(
    year_selection  
).transform_filter(
    year_selection 
).properties(
    width=400,
    height=200
)

total_chart

alt.Chart(...)

Além disso, apenas para fins de curiosidade, podemos ver como fica o rastro da bolinha num gráfico estático, como mostrado abaixo:

In [51]:
bolinha = alt.Chart(every).mark_point().encode(
    x=alt.X('Year:Q', title='Ano', scale=alt.Scale(domain=[1900, 2017])), 
    y=alt.Y('variation:Q', title='Variação total', scale=alt.Scale(domain=[-0.9972122154018693, 8410.69])),  
    color=alt.Color('Entity:N', legend=alt.Legend(title='Entidade')),  
    tooltip=['Year', 'variation', 'Entity']  
).properties(
    width=400,
    height=200
)

bolinha

alt.Chart(...)

Agora, com os dois gráficos prontos, vamos observar a visualização com ambos juntos:

In [52]:
chart = entity_chart | total_chart
chart

alt.HConcatChart(...)

Agora, para uma visualização um pouco melhor para o entendimento de como se deu a variação, faremos uma gráfico de linhas com pontos estático.


In [53]:


estatic_chart = alt.Chart(every).mark_line(
    strokeWidth=2,
    interpolate='monotone'
).encode(
    x=alt.X('Year:Q', title='Ano', scale=alt.Scale(domain=[1900, 2017])), 
    y=alt.Y('variation:Q', title='Variação'),  
    color=alt.Color('Entity:N', legend=alt.Legend(title='Entidade')),  
    tooltip=['Year', 'variation', 'Entity']  
).properties(
    width=400,
    height=200
).interactive()

estatic = estatic_chart + estatic_chart.mark_circle()
estatic

alt.LayerChart(...)

Com isso, podemos observar as mortes por desastres naturais e suas variações ao longo do tempo de maneiras diferentes.

### Exemplo 3.1 (Eliani): Iris

Nesse exemplo faremos a apresentação gráfica do conjunto de dados chamado `iris` da biblioteca `vega_datasets`. Esse conjunto guarda informações sobre o comprimento e largura das pétalas e sépalas de algumas espécies de flores.

In [57]:
# Listar os datasets disponíveis inspecionando os atributos do módulo 'data'
#print(dir(vega_datasets.data))

iris = data.iris()

# Visualizando o arquivo escolhido:
df = pd.DataFrame(iris)
print(df.head())

# Quantidade de linhas e colunas:
iris.shape


   sepalLength  sepalWidth  petalLength  petalWidth species
0          5.1         3.5          1.4         0.2  setosa
1          4.9         3.0          1.4         0.2  setosa
2          4.7         3.2          1.3         0.2  setosa
3          4.6         3.1          1.5         0.2  setosa
4          5.0         3.6          1.4         0.2  setosa


(150, 5)

In [58]:
# Vendo os dados sobre a espécie setosa:
irissetosa = iris.loc[iris['species'] == 'setosa']

irissetosa.head(5)

sepalLength  sepalWidth  petalLength  petalWidth species
0          5.1         3.5          1.4         0.2  setosa
1          4.9         3.0          1.4         0.2  setosa
2          4.7         3.2          1.3         0.2  setosa
3          4.6         3.1          1.5         0.2  setosa
4          5.0         3.6          1.4         0.2  setosa

In [59]:
# Dados nominais: Espécie
# Quantidade de setosa de acordo com a largura da sépala:
alt.Chart(irissetosa).mark_point().encode(
    alt.X('sepalWidth:O')
)

alt.Chart(...)

In [60]:
# Visualização de distribuição das variáveis numéricas por espécie
chart = alt.Chart(df).mark_bar().encode(
    alt.X('sepalLength:Q', bin=True),
    alt.Y('count():Q'),
    alt.Color('species:N')
).properties(
    title='Distribuição do Comprimento da Sépala por Espécie'
)

chart.show()

alt.Chart(...)

In [61]:
# Gráfico de dispersão com comprimento no eixo X, largura no eixo Y e cor por espécie
scatter = alt.Chart(df).mark_point().encode(
    alt.X('petalLength:Q', title='Comprimento da Pétala'),
    alt.Y('petalWidth:Q', title='Largura da Pétala'),
    alt.Color('species:N', title='Espécie'),
    tooltip=['species:N', 'petalLength:Q', 'petalWidth:Q']  # Exibir dados ao passar o mouse
).properties(
    title='Comprimento vs Largura das Pétalas por Espécie'
)

scatter.show()

alt.Chart(...)

Perceba que no gráfico acima podemos perceber uma relação direta entre o tamanho da pétala e a espécie de flor.

### Exemplo 3.2 (Eliani): População

Nesse exemplo faremos a apresentação gráfica do conjunto de dados chamado `population` da biblioteca `vega_datasets`. Esse conjunto guarda informações sobre a quantidade de homens e mulheres em cada ano dividida por faixa etária.


In [63]:
pop = data.population()

# Visualizando o arquivo escolhido:
d = pd.DataFrame(pop)
print(d.head())

# Quantidade de linhas e colunas:
pop.shape

   year  age  sex   people
0  1850    0    1  1483789
1  1850    0    2  1450376
2  1850    5    1  1411067
3  1850    5    2  1359668
4  1850   10    1  1260099


(570, 4)

In [64]:
# Agrupar por ano e sexo e somar a população de cada grupo
population_by_sex = d.groupby(['year', 'sex'])['people'].sum().reset_index()

# Substituir os valores de 'sex' (1 = Masculino, 2 = Feminino)
d['sex'] = d['sex'].replace({1: 'Masculino', 2: 'Feminino'})

# Criar um gráfico de linha para visualizar a diferença de população por sexo ao longo dos anos
chart = alt.Chart(population_by_sex).mark_line().encode(
    x='year:O',
    y='people:Q',
    color='sex:N',  # Diferenciar por sexo
    tooltip=['year:O', 'people:Q', 'sex:N']  # Mostrar dados ao passar o mouse
).properties(
    title='Evolução da População ao Longo dos Anos por Sexo'
)

chart.show()


alt.Chart(...)

In [65]:
# Gráfico de barras empilhadas para distribuição de pessoas por faixa etária e sexo
chart = alt.Chart(d).mark_bar().encode(
    x='age:O',
    y='people:Q',
    color='sex:N',
    column='year:O',
    tooltip=['year:O', 'age:O', 'people:Q', 'sex:N']
).properties(
    title='Distribuição de População por Faixa Etária, Sexo e Ano'
)

chart.show()

alt.Chart(...)

Por meio desses gráficos podemos observar que a população feminina nos anos de 1950 a 2000 se tornou a maioria, o que pode ser explicado pela maior expectativa de vida das mulheres nas últimas décadas.

### Exemplo 4.1 (Erique)
Indíce de fecundidade dos países ao longo dos anos.

In [93]:
# Carregar a base de dados countries do vega_datasets
countries = data.countries()

# Ler a coluna de dados ano (year) como números inteiros
countries['year'] = countries['year'].astype(int)

# Adcionar o controle deslizante variando o ano da linha de dados
select_year = alt.selection_point(
    name='Year',
    fields=['year'],
    value={'year': 1955},
    bind=alt.binding_range(min=countries['year'].min(), max=countries['year'].max(), step=5)
)

# Criação do gráfico de barras mostrando a fecundidade de cada país na base de dados
bar_chart = alt.Chart(countries).mark_bar().encode(
    x=alt.X('fertility:Q', title='Fecundidade'),
    y=alt.Y('country:N', sort='-x', title='Países'),
    color='country:N',
    tooltip=['country', 'fertility', 'year']
).add_selection(
    select_year
).transform_filter(
    select_year
).properties(
    title='Indice de Fecundidade dos países a cada ano',
    width=700,
    height=500
)
bar_chart

C:\Users\taina\AppData\Local\Temp\ipykernel_21452\3858762942.py:21: AltairDeprecationWarning: 
Deprecated since `altair=5.0.0`. Use add_params instead.
  ).add_selection(


alt.Chart(...)

### Exemplo 4.2 (Erique)
Classificação média dos filmes de acordo com o gênero pelo IMDB.

In [67]:
# Carregar a base de dados movies do vega_datasets
movies = data.movies()

# Criação do gráfico de barras mostrando a classificação média do IMDB por gênero de filme
bar_chart = alt.Chart(movies).mark_bar().encode(
    x=alt.X('mean(IMDB_Rating):Q', title='Nota média IMDB'),
    y=alt.Y('Major_Genre:N', sort='-x', title='Gênero'),
    color=alt.Color('Major_Genre:N', legend=None),
    tooltip=['Major_Genre', 'mean(IMDB_Rating):Q']
).properties(
    title='Average IMDB Rating by Major Genre',
    width=800,
    height=400
)
bar_chart

alt.Chart(...)

### Exemplo 5.1 (Joênio): Um Pequeno Estudo de Estacionariedade

Este exemplo apresenta um passo-a-passo introdutório para analisar a estacionariedade de um índice financeiro, como o S&P 500. O objetivo é investigar se as cotações do índice exibem características de estacionariedade, utilizando visualizações gráficas. Neste caso, os gráficos serão gerados com a biblioteca Altair, e o conjunto de dados utilizado será o sp500, disponível no pacote vega_datasets.

In [68]:
sp500 = data.sp500()

O primeiro passo será criar um gráfico de linhas para visualizar a evolução do índice ao longo do tempo. Essa análise é necessária para identificar possíveis tendências ou padrões que possam indicar sua ausência:

In [69]:
chart = alt.Chart(sp500).mark_line().encode(
    x = alt.X('date:T', title = 'Anos'),
    y = alt.Y('price:Q', title = 'Cotação do Índice S&P 500'),
    tooltip = ['date:T', 'price:Q']
).properties(
    title = 'Cotação do Índice S&P 500 ao Longo do Tempo',
    width = 800,
    height = 400
)

chart

alt.Chart(...)

Sem a identificação de uma clara ausência de estacionariedade, devemos avaliar a consistência das flutuações das cotações do índice ao longo do tempo:

In [70]:
chart_diff = alt.Chart(sp500).transform_window(
    lag_price = 'lag(price)',
    sort = [{'field': 'date'}]
).transform_calculate(
    diff = 'datum.price - datum.lag_price'
).mark_line().encode(
    x = alt.X('date:T', title='Anos'),
    y = alt.Y('diff:Q', title='Diferença nas Cotações'),
    tooltip = ['date:T', 'diff:Q']
).properties(
    title = 'Variação das Cotações do S&P 500 pelo método de diferenças',
    width = 800,
    height = 400
)

chart_diff

alt.Chart(...)

Por fim, vamos adicionar uma média móvel de 30, para suavizar oscilações, e assim, analisar tendências:

In [71]:
chart_mm = alt.Chart(sp500).transform_window(
    rolling_mean = 'mean(price)',
    frame = [-15, 15],
    sort = [{'field': 'date'}]
).mark_line(color = 'orange').encode(
    x = 'date:T',
    y = 'rolling_mean:Q',
    tooltip = ['date:T', 'rolling_mean:Q']
).properties(
    title = "Média Móvel (30 Dias) do S&P 500",
    width = 800,
    height = 400
)

chart_mm + chart

alt.LayerChart(...)

Como há uma tendência constante observada no índice, tanto pelo método das diferenças quanto pela análise de média movel, podemos considerar que o índice é aproximadamente estacionário.

Embora o estudo completo da estacionariedade de índices envolva uma análise muito mais profunda, este exemplo serve como uma excelente introdução a alguns conceitos fundamentais e à aplicação de visualizações de dados.

In [72]:
movies_url = 'https://cdn.jsdelivr.net/npm/vega-datasets@1/data/movies.json'
movies = pd.read_json(movies_url) 

### Exemplo 6 (Pedro Barbosa): Gráficos com filmes

Vasculhando a base movie, fiquei curioso para saber quais os melhores filmes, os anos que foram alcançados pelo dataframe, visto que não é atualizada há algum tempo, e mais informações. Partindo disso, criei dois gráficos: um que separa os filmes em gêneros e ranqueia, e outro que indica o ano de lançamento de um filme e sua respectiva nota no IMDB.

No primeiro, me baseei no que aprendi no capítulo 1 sobre interatividade, eu queria que meu gráfico fosse interativo e apresentasse tooltip. Como marca, escolhi a marca de círculo que vi no capítulo 2, pois achei mais interessante visualmente. As cores representam de forma redundante o gênero, o que enfatiza essa categoria. Tive dificuldade para ler esse arquivo json, pois eu não sabia lidar com ele, pesquisei na internet e aprendi. Depois, percebi durante a aula do dia 22 de janeiro que o pandas lia json de forma mais fácil (antes eu havia baixado o dataframe e havia usado a biblioteca json, agora uso *pd.read_json()*).

Tive dificuldades para implementar títulos na *tooltip* do gráfico 1, aparecia 'NaN' no lugar do nome. Pedi ajuda, me disseram que eu deveria indicar o tipo de dado que estava sendo lido em "Title", indiquei que era um nome de filme com N. Depois de corrigido, o gráfico ficou assim: 

In [73]:
alt.Chart(movies).mark_point(filled=True).encode(
    x="Major_Genre",
    y="IMDB_Rating",
    color="Major_Genre",
    tooltip=["Title:N","Release_Date","IMDB_Rating"]
).interactive()

alt.Chart(...)

Os 3 melhores filmes são The Godfather (O Poderoso Chefão), The Shawshank Redemption (Um Sonho de Liberdade) e Inception (A Origem), com mensão honrosa para o O Poderoso Chefão parte 2.

Para o gráfico 2, não tive dificuldade , pois os problemas que lidei no gráfico 1 foram bem resolvidos. Esse gráfico de Data de lançamento vs. nota no IMDB indica uma tendência de filmes antigos registrados no *datframe* serem melhores do que grande parte dos filmes atuais. A pergunta sobre os anos que o dataframe alcança foi respondida, pois a maioria dos pontos não passam de 2010. Depois de 2010, existem alguns erros, por exemplo "The Best Years of our Lives",que foi lançado em 1946, está registrado como 2046.

In [74]:
alt.Chart(movies).mark_point(filled=True).encode(
  x='Release_Date:T',
  y='IMDB_Rating:Q',
  color='Major_Genre:N',
  tooltip=["Title:N","Release_Date:T"]
).interactive()


alt.Chart(...)

### Exemplo 7 (Vinicius Prestes)

In [75]:
cars = data.cars()

# Gráfico de dispersão dos carros mostrando relação entre Horsepower e Miles per Gallon (MPG)
scatter_plot = alt.Chart(cars).mark_point().encode(
    x=alt.X('Horsepower:Q', title='Horsepower'),
    y=alt.Y('Miles_per_Gallon:Q', title='Miles per Gallon (MPG)'),
    color='Origin:N',
    tooltip=['Name:N', 'Horsepower:Q', 'Miles_per_Gallon:Q']
).properties(
    title='Relação entre Horsepower e MPG',
    width=600,
    height=400
)

# Exibir o gráfico de dispersão
scatter_plot

alt.Chart(...)

Carregar e visualizar o dataset "movies"

In [76]:
# Celula 3: Carregar e visualizar o dataset "movies"
# Dataset 2: movies
movies = data.movies()

# Gráfico de barras mostrando a contagem de filmes por gênero
bar_chart = alt.Chart(movies).mark_bar().encode(
    x=alt.X('count():Q', title='Número de Filmes'),
    y=alt.Y('Major_Genre:N', title='Gênero', sort='-x'),
    color='Major_Genre:N',
    tooltip=['Major_Genre:N', 'count():Q']
).properties(
    title='Contagem de Filmes por Gênero',
    width=600,
    height=400
)

# Exibir o gráfico de barras
bar_chart


alt.Chart(...)

### Exemplo 8 (Arthur Zaneti)

In [77]:
# Carregar o conjunto de dados "barley"
barley = data.barley()

# Criar o gráfico de barras
chart = alt.Chart(barley).mark_bar().encode(
    x=alt.X('mean(yield):Q', title='Produção média (bushels/acre)'), #Unidade usual pra medidas agrícolas nos Estados Unidos, é mais ou menos 35.24litros/4.047m^2
    y=alt.Y('site:N', title='Sítio', sort='-x'),
    color=alt.Color('site:N', legend=None),
    tooltip=['site:N', 'mean(yield):Q']
).properties(
    width=600,
    height=400,
    title='Produção Média de Cevada por Sítio em Minnesota'
).interactive()

chart.show()

alt.Chart(...)

### Exemplo 9.1 (Tainá): Seattle Weather

Vamos criar um exemplo a partir da base de dados do clima de Seattle.

In [78]:
seattle_weather = data.seattle_weather()
seattle_weather.head()

date  precipitation  temp_max  temp_min  wind  weather
0 2012-01-01            0.0      12.8       5.0   4.7  drizzle
1 2012-01-02           10.9      10.6       2.8   4.5     rain
2 2012-01-03            0.8      11.7       7.2   2.3     rain
3 2012-01-04           20.3      12.2       5.6   4.7     rain
4 2012-01-05            1.3       8.9       2.8   6.1     rain

Para melhor visualização, renomearemos as colunas da tabela.

In [79]:
seattle_weather.columns = ["Data", "Precipitação", "Temperatura máxima", "Temperatura mínima", "Vento", "Clima"]
seattle_weather.head()

Data  Precipitação  Temperatura máxima  Temperatura mínima  Vento  \
0 2012-01-01           0.0                12.8                 5.0    4.7   
1 2012-01-02          10.9                10.6                 2.8    4.5   
2 2012-01-03           0.8                11.7                 7.2    2.3   
3 2012-01-04          20.3                12.2                 5.6    4.7   
4 2012-01-05           1.3                 8.9                 2.8    6.1   

     Clima  
0  drizzle  
1     rain  
2     rain  
3     rain  
4     rain

Gostaríamos de analisar as condições climáticas de Seattle no ano de 2012. Para isso, vamos filtrar o _data frame_ para as observações feitas apenas nesse ano.

In [80]:
seattle_2012_weather = seattle_weather[seattle_weather['Data'].dt.year == 2012]
seattle_2012_weather

Data  Precipitação  Temperatura máxima  Temperatura mínima  Vento  \
0   2012-01-01           0.0                12.8                 5.0    4.7   
1   2012-01-02          10.9                10.6                 2.8    4.5   
2   2012-01-03           0.8                11.7                 7.2    2.3   
3   2012-01-04          20.3                12.2                 5.6    4.7   
4   2012-01-05           1.3                 8.9                 2.8    6.1   
..         ...           ...                 ...                 ...    ...   
361 2012-12-27           4.1                 7.8                 3.3    3.2   
362 2012-12-28           0.0                 8.3                 3.9    1.7   
363 2012-12-29           1.5                 5.0                 3.3    1.7   
364 2012-12-30           0.0                 4.4                 0.0    1.8   
365 2012-12-31           0.0                 3.3                -1.1    2.0   

       Clima  
0    drizzle  
1       rain  
2       rain  
3       rain  
4       rain  
..       ...  
361     rain  
362     rain  
363     rain  
364  drizzle  
365  drizzle  

[366 rows x 6 columns]

Agruparemos as observações por cada mês, selecionando as temperaturas máxima e mínima, as médias de precipitação e vento e, por fim, a moda do clima. 

In [81]:
seattle_2012_weather_by_month = seattle_2012_weather.groupby(seattle_2012_weather['Data'].dt.month) \
    .agg(   
        TemperaturaMinima = ("Temperatura mínima", "min"),
        TemperaturaMaxima = ("Temperatura máxima", "max"), 
        PrecipitacaoMedia = ("Precipitação", "mean"),
        VentoMedio = ("Vento", "mean"), 
        Clima = ("Clima", pd.Series.mode)) \
    .reset_index()
    
seattle_2012_weather_by_month

Data  TemperaturaMinima  TemperaturaMaxima  PrecipitacaoMedia  VentoMedio  \
0      1               -3.3               12.8           5.590323    3.900000   
1      2               -2.2               16.1           3.182759    3.903448   
2      3               -1.7               15.6           5.903226    4.248387   
3      4                1.7               23.3           2.270000    3.373333   
4      5                3.9               26.7           1.683871    3.354839   
5      6                6.1               24.4           2.503333    3.083333   
6      7                9.4               28.3           0.848387    2.877419   
7      8               10.0               34.4           0.000000    2.829032   
8      9                7.8               32.2           0.030000    2.646667   
9     10                3.3               23.9           5.493548    3.532258   
10    11               -0.6               17.8           7.016667    3.220000   
11    12               -1.7               13.3           5.612903    3.832258   

          Clima  
0          rain  
1          rain  
2          rain  
3          rain  
4          rain  
5          rain  
6   [rain, sun]  
7           sun  
8           sun  
9          rain  
10         rain  
11         rain

Agora, renomearemos as colunas e os meses.

In [82]:
seattle_2012_weather_by_month.columns = ['Mês', 'Temperatura mínima', 'Temperatura máxima', 'Precipitação média', 'Vento médio', 'Clima']
seattle_2012_weather_by_month['Mês'] = ['Janeiro', 'Fevereiro', 'Março', 'Abril', 'Maio', 'Junho', 'Julho', 'Agosto', 'Setembro', 'Outubro', 'Novembro', 'Dezembro']

seattle_2012_weather_by_month

Mês  Temperatura mínima  Temperatura máxima  Precipitação média  \
0     Janeiro                -3.3                12.8            5.590323   
1   Fevereiro                -2.2                16.1            3.182759   
2       Março                -1.7                15.6            5.903226   
3       Abril                 1.7                23.3            2.270000   
4        Maio                 3.9                26.7            1.683871   
5       Junho                 6.1                24.4            2.503333   
6       Julho                 9.4                28.3            0.848387   
7      Agosto                10.0                34.4            0.000000   
8    Setembro                 7.8                32.2            0.030000   
9     Outubro                 3.3                23.9            5.493548   
10   Novembro                -0.6                17.8            7.016667   
11   Dezembro                -1.7                13.3            5.612903   

    Vento médio        Clima  
0      3.900000         rain  
1      3.903448         rain  
2      4.248387         rain  
3      3.373333         rain  
4      3.354839         rain  
5      3.083333         rain  
6      2.877419  [rain, sun]  
7      2.829032          sun  
8      2.646667          sun  
9      3.532258         rain  
10     3.220000         rain  
11     3.832258         rain

Finalmente, podemos gerar um gráfico para esses dados.

Vamos fazer um climograma, exibindo, para cada mês, as temperaturas máximas e mínimas e a precipitação média.

In [83]:
barras_de_temperatura = alt.Chart(seattle_2012_weather_by_month).mark_bar().encode(
    alt.X('Mês'),
    alt.Y('Temperatura mínima'),
    alt.Y2('Temperatura máxima')
)

linha_de_precipitacao = alt.Chart(seattle_2012_weather_by_month).mark_line(opacity=0.8, color='red').encode(
    alt.X('Mês'),
    alt.Y('Precipitação média')
)

alt.layer(barras_de_temperatura, linha_de_precipitacao).resolve_scale(y='independent').properties(width=600)

alt.LayerChart(...)

### Exemplo 9.2 (Tainá): Vetores de vento

Vamos exibir um mapa de vetores de vento por meio da base de dados `windvectors`.

In [84]:
windvectors = data.windvectors()
windvectors

longitude  latitude  dir  dirCat  speed
0         0.125    45.125  228     225   3.12
1         0.375    45.125  228     225   3.24
2         0.625    45.125  229     225   3.34
3         0.875    45.125  229     225   3.44
4         1.125    45.125  228     225   3.48
...         ...       ...  ...     ...    ...
4795     -1.125    59.875  155     150   5.96
4796     -0.875    59.875  154     150   6.34
4797     -0.625    59.875  153     150   6.71
4798     -0.375    59.875  152     150   7.09
4799     -0.125    59.875  152     150   7.48

[4800 rows x 5 columns]

Renomearemos as colunas para melhor visualização.

In [85]:
windvectors.columns = ['Longitude', 'Latitude', 'Direção', 'Categoria da direção', 'Velocidade']
windvectors.head()

Longitude  Latitude  Direção  Categoria da direção  Velocidade
0      0.125    45.125      228                   225        3.12
1      0.375    45.125      228                   225        3.24
2      0.625    45.125      229                   225        3.34
3      0.875    45.125      229                   225        3.44
4      1.125    45.125      228                   225        3.48

Agora, podemos exibir essas informações visualmente. Utilizaremos a direção do vento para determinar o ângulo da marca gráfica e codificaremos a velocidade através da cor.

In [86]:
wind_map = alt.Chart(windvectors).mark_text(text="|", fontWeight="bold").encode(
    alt.X('Latitude', scale=alt.Scale(zero=False, nice=False)),
    alt.Y('Longitude', scale=alt.Scale(zero=False, nice=False)),
    alt.Color('Velocidade'),
    alt.Tooltip(['Latitude', 'Longitude']),
    angle=alt.Angle('Direção:Q', scale=None)
).interactive()

wind_map

alt.Chart(...)

### Exemplo 10.1 (Pedro Alberti): Piramide etária

Inicialmente a minha ideia era ver como eu poderia manipular a visualização dados de forma a levar a uma conclusão falsa e depois esclarescer.

In [87]:
population = data.population()

population # para visualizar o dataset

year  age  sex   people
0    1850    0    1  1483789
1    1850    0    2  1450376
2    1850    5    1  1411067
3    1850    5    2  1359668
4    1850   10    1  1260099
..    ...  ...  ...      ...
565  2000   80    2  3221898
566  2000   85    1   970357
567  2000   85    2  1981156
568  2000   90    1   336303
569  2000   90    2  1064581

[570 rows x 4 columns]

In [88]:
population = data.population()

select_year = alt.selection_point(
    name='select',
    fields=['year'],
    init={'year': 1970},
    bind = alt.binding_range(min=1850, max=2000, step=10),
    value=1850
) #criando um filtro para o ano

chart = alt.Chart(population).mark_bar(opacity=1).encode(
    alt.Y('age:N', title='Faixa Etária'),  
    alt.X('people:Q', title='População'),       
    alt.Tooltip('people'), 
    color=alt.condition(
        alt.datum.sex == 1,  # Condição para 'sex == 1'
        alt.value('blue'),   # Cor para sex == 1
        alt.value('green')     # Cor para o caso contrário (sex == 2)
    ), 
    row=alt.Row('year:O', title='Ano'),          
).add_params(select_year).transform_filter(select_year)
#considerei fazer as linhas em paralelo ao invés de em série mas ficaria muito extenso e optei por manter
chart

alt.Chart(...)

<span style="color:deeppink">Inicialmente</span> vale comentar que de fato na base de dados não há informações sobre 1890. O <span style="color:deeppink">primeiro</span> ponto é que quanto a evolução da piramide etária o panorama começa a mudar em 1920 mas entre 1940-1950 há uma grande queda no número de adultos, o que é interessante pois assumindo que houve esta grande perda devido a segunda guerra mundial não grande impacto no tempo da primeira, nos levando a crer que possa ter sido um país muito presente na segunda e pouco na primeira, como EUA ou Japão, análise importante dado que não informação sobre o país feito na base de dados. O <span style="color:deeppink">segundo</span> ponto interessante é que a partir da decáda de 60 o genero verde cresce muito em relação ao azul nas idades maiores que 60 e em especial acima dos 70. E dado que atualmente há de fato maior número de mulheres idosas que homens idosos, conclui-se que o verde seria o sexo feminino.

Esclarescendo o <span style="color:deeppink">primeiro</span> ponto : na verdade não houve uma redução na população adulta mas como houve muitas crianças o gráfico foi redimensionado, apesar de ser realmente interessante o porquê desse outlier durante 40-60 , tais motivos não são o foco no momento. E quanto ao <span style="color:deeppink">segundo</span> ponto se esse fosse o caso teriamos observado uma grande queda no sexo azul durante o periodo das guerras, além de outras detalhes que não foram analisados apropriadamente.

### Exemplo 10.2 (Pedro Alberti): Perfil de carro 

A minha ideia inicial seria traçar um perfil para o que cada comprador deseja entre 2 categorias, economia de gasolina e aceleração. Apesar de terem outras categorias na própria tabela como potencia, cilindragem e peso optei por apenas essas por considerar como principais.

In [89]:
carros = data.cars()

carros # para visualizar o dataset

Name  Miles_per_Gallon  Cylinders  Displacement  \
0    chevrolet chevelle malibu              18.0          8         307.0   
1            buick skylark 320              15.0          8         350.0   
2           plymouth satellite              18.0          8         318.0   
3                amc rebel sst              16.0          8         304.0   
4                  ford torino              17.0          8         302.0   
..                         ...               ...        ...           ...   
401            ford mustang gl              27.0          4         140.0   
402                  vw pickup              44.0          4          97.0   
403              dodge rampage              32.0          4         135.0   
404                ford ranger              28.0          4         120.0   
405                 chevy s-10              31.0          4         119.0   

     Horsepower  Weight_in_lbs  Acceleration       Year  Origin  
0         130.0           3504          12.0 1970-01-01     USA  
1         165.0           3693          11.5 1970-01-01     USA  
2         150.0           3436          11.0 1970-01-01     USA  
3         150.0           3433          12.0 1970-01-01     USA  
4         140.0           3449          10.5 1970-01-01     USA  
..          ...            ...           ...        ...     ...  
401        86.0           2790          15.6 1982-01-01     USA  
402        52.0           2130          24.6 1982-01-01  Europe  
403        84.0           2295          11.6 1982-01-01     USA  
404        79.0           2625          18.6 1982-01-01     USA  
405        82.0           2720          19.4 1982-01-01     USA  

[406 rows x 9 columns]

In [90]:
carros['Year'] = carros['Year'].dt.year # a data estava num formato ruim de trabalhar, então foi modificada de forma a facilitar a codificação 

select_year = alt.selection_point(
    name='select',
    fields=['Year'],
    init={'Year': 1970},
    bind = alt.binding_range(min=1970, max=1982, step=1),
    value=1970
) #criando um filtro para o ano

alt.Chart(carros).mark_circle(opacity=1).encode(
    alt.X('Acceleration'),
    alt.Y('Miles_per_Gallon'),
    alt.Color('Origin'),
    alt.Tooltip('Name')
).add_params(select_year).transform_filter(select_year)

alt.Chart(...)

Quanto a proposta inicial podemos traçar o seguinte perfil por região de feitura : os carros europeus se mostram muito economicos onde apesar de uma leve queda ainda se mostram bem nesse quesito. Os carros americanos que iniciaram piores nos 2 aspectos conseguiram ao longo do tempo uma grande melhora em aceleração onde ganha protagonismo. Por outro lado os carros japoneses conseguem fazer um ótimo balanço entre as 2 características e sempre se faz num bom posicionamento quando visto na média por região.

Espero ter ajudado na tomada de decisão do seu carro ideal. Onde apesar de diversos outros fatores, tentei torna-la mais objetiva e simples.

### Exemplo 11.1 (José): taxa de emprego nos Estados Unidos por categoria


Separamos os empregos pela categoria sendo, privao(private), publico(government), ou setores não agricola(nofarm).

In [91]:
# Load the dataset
us_employment = data.us_employment()

# Melt the dataset for easier plotting
melted_data = us_employment.melt(
    id_vars='month',
    value_vars=['nonfarm', 'private', 'government'],
    var_name='categoria',
    value_name='emprego'
)

# Convert 'month' to a datetime format
melted_data['month'] = pd.to_datetime(melted_data['month'])

# Create the line chart
chart = alt.Chart(melted_data).mark_line().encode(
    x='month:T',  # Temporal x-axis for the month
    y='emprego:Q',  # Quantitative y-axis for employment
    color='categoria:N',  # Color by category
    tooltip=['month:T', 'categoria:N', 'emprego:Q']  # Tooltips for interaction
).properties(
    title='Tendências de Emprego nos EUA por Categoria',
    width=800,
    height=400
)

# Show the chart
chart.show()


alt.Chart(...)

### Exemplo 11.2 (José): Por setores
Separamos os empregos pelos diferentes setores presentes no Estados Unidos,produção de bens(goods_producing), prestação de serviços(service_providing), manufatura(manufacturing), construção(construction), lazer e hospitalidade(leisure_and_hospitality), educação e serviço de saúde(education_and_health_services)

In [92]:

selected_columns = [
    'goods_producing', 'service_providing', 'manufacturing',
    'construction', 'leisure_and_hospitality', 'education_and_health_services'
]

average_employment = us_employment[selected_columns].mean().reset_index()
average_employment.columns = ['setor', 'emprego_medio']

chart = alt.Chart(average_employment).mark_bar().encode(
    x=alt.X('setor:N', title='Setor de Emprego', sort='-y'),
    y=alt.Y('emprego_medio:Q', title='Emprego Médio (em milhares)'), 
    color='setor:N',  
    tooltip=['setor:N', 'emprego_medio:Q']  
).properties(
    title='Emprego Médio por Setor nos EUA',
    width=600,
    height=400
)

chart.show()

alt.Chart(...)